# Computer Vision Nanodegree

## Project: Image Captioning

---

In this notebook, you will train your CNN-RNN model.  

You are welcome and encouraged to try out many different architectures and hyperparameters when searching for a good model.

This does have the potential to make the project quite messy!  Before submitting your project, make sure that you clean up:
- the code you write in this notebook.  The notebook should describe how to train a single CNN-RNN architecture, corresponding to your final choice of hyperparameters.  You should structure the notebook so that the reviewer can replicate your results by running the code in this notebook.  
- the output of the code cell in **Step 2**.  The output should show the output obtained when training the model from scratch.

This notebook **will be graded**.  

Feel free to use the links below to navigate the notebook:
- [Step 1](#step1): Training Setup
- [Step 2](#step2): Train your Model
- [Step 3](#step3): (Optional) Validate your Model

<a id='step1'></a>
## Step 1: Training Setup

In this step of the notebook, you will customize the training of your CNN-RNN model by specifying hyperparameters and setting other options that are important to the training procedure.  The values you set now will be used when training your model in **Step 2** below.

You should only amend blocks of code that are preceded by a `TODO` statement.  **Any code blocks that are not preceded by a `TODO` statement should not be modified**.

### Task #1

Begin by setting the following variables:
- `batch_size` - the batch size of each training batch.  It is the number of image-caption pairs used to amend the model weights in each training step. 
- `vocab_threshold` - the minimum word count threshold.  Note that a larger threshold will result in a smaller vocabulary, whereas a smaller threshold will include rarer words and result in a larger vocabulary.  
- `vocab_from_file` - a Boolean that decides whether to load the vocabulary from file. 
- `embed_size` - the dimensionality of the image and word embeddings.  
- `hidden_size` - the number of features in the hidden state of the RNN decoder.  
- `num_epochs` - the number of epochs to train the model.  We recommend that you set `num_epochs=3`, but feel free to increase or decrease this number as you wish.  [This paper](https://arxiv.org/pdf/1502.03044.pdf) trained a captioning model on a single state-of-the-art GPU for 3 days, but you'll soon see that you can get reasonable results in a matter of a few hours!  (_But of course, if you want your model to compete with current research, you will have to train for much longer._)
- `save_every` - determines how often to save the model weights.  We recommend that you set `save_every=1`, to save the model weights after each epoch.  This way, after the `i`th epoch, the encoder and decoder weights will be saved in the `models/` folder as `encoder-i.pkl` and `decoder-i.pkl`, respectively.
- `print_every` - determines how often to print the batch loss to the Jupyter notebook while training.  Note that you **will not** observe a monotonic decrease in the loss function while training - this is perfectly fine and completely expected!  You are encouraged to keep this at its default value of `100` to avoid clogging the notebook, but feel free to change it.
- `log_file` - the name of the text file containing - for every step - how the loss and perplexity evolved during training.

If you're not sure where to begin to set some of the values above, you can peruse [this paper](https://arxiv.org/pdf/1502.03044.pdf) and [this paper](https://arxiv.org/pdf/1411.4555.pdf) for useful guidance!  **To avoid spending too long on this notebook**, you are encouraged to consult these suggested research papers to obtain a strong initial guess for which hyperparameters are likely to work best.  Then, train a single model, and proceed to the next notebook (**3_Inference.ipynb**).  If you are unhappy with your performance, you can return to this notebook to tweak the hyperparameters (and/or the architecture in **model.py**) and re-train your model.

### Question 1

**Question:** Describe your CNN-RNN architecture in detail.  With this architecture in mind, how did you select the values of the variables in Task 1?  If you consulted a research paper detailing a successful implementation of an image captioning model, please provide the reference.

**Answer:** here I use Resnet50 as an encoder, the encoder will produce feature vector images. The feature vector image is then inserted into the RNN network with the LSTM cell decoder (I did not apply attention). in [this paper](https://arxiv.org/pdf/1411.4555.pdf), using SGD, but here im using Adam because i've tried and get better result. Same like facial key-points projects. 

like architecture in picture on notebook 1, my RNN:
1. word embedding
2. LTSM cell (dropout =0.5)
3. hidden layer
4. linear layer

vocab_threshold i choose 5 same as paper, embed_size i chosee 256 and give batchnormalisation, hidden_size i choose 1024 and give dropout 0.5, embed_size and hidden_size just guesting.


### (Optional) Task #2

Note that we have provided a recommended image transform `transform_train` for pre-processing the training images, but you are welcome (and encouraged!) to modify it as you wish.  When modifying this transform, keep in mind that:
- the images in the dataset have varying heights and widths, and 
- if using a pre-trained model, you must perform the corresponding appropriate normalization.

### Question 2

**Question:** How did you select the transform in `transform_train`?  If you left the transform at its provided value, why do you think that it is a good choice for your CNN architecture?

**Answer:** udacity has provided a suitable and suitable transform train for resnet50, so I don't think I need to make any significant changes.

### Task #3

Next, you will specify a Python list containing the learnable parameters of the model.  For instance, if you decide to make all weights in the decoder trainable, but only want to train the weights in the embedding layer of the encoder, then you should set `params` to something like:
```
params = list(decoder.parameters()) + list(encoder.embed.parameters()) 
```

### Question 3

**Question:** How did you select the trainable parameters of your architecture? Why do you think this is a good choice?

**Answer:** I only took the last vector layer of resnet50 plus the RNN parameters that have not been trained at all like the connet layer resnet50 pretrained.

### Task #4

Finally, you will select an [optimizer](http://pytorch.org/docs/master/optim.html#torch.optim.Optimizer).

### Question 4

**Question:** How did you select the optimizer used to train your model?

**Answer:** slightly different from the reference paper, I chose Adam optimezer with lr = 0.0001 because based on some data and experience, Adam gave a lower loss value compared to SGD used in the paper.

In [1]:
import torch
import torch.nn as nn
from torchvision import transforms
import sys
sys.path.append('/opt/cocoapi/PythonAPI')
from pycocotools.coco import COCO
from data_loader import get_loader
from model import EncoderCNN, DecoderRNN
import math
import nltk
nltk.download('punkt')


## TODO #1: Select appropriate values for the Python variables below.
batch_size = 16          # batch size
vocab_threshold = 5        # minimum word count threshold
vocab_from_file = True    # if True, load existing vocab file
embed_size = 256           # dimensionality of image and word embeddings
hidden_size = 1024          # number of features in hidden state of the RNN decoder
num_epochs = 1             # number of training epochs
save_every = 1             # determines frequency of saving model weights
print_every = 100          # determines window for printing average loss
log_file = 'training_log.txt'       # name of file with saved training loss and perplexity

# (Optional) TODO #2: Amend the image transform below.
transform_train = transforms.Compose([ 
    transforms.Resize(256),                          # smaller edge of image resized to 256
    transforms.RandomCrop(224),                      # get 224x224 crop from random location
    transforms.RandomHorizontalFlip(),               # horizontally flip image with probability=0.5
    transforms.ToTensor(),                           # convert the PIL Image to a tensor
    transforms.Normalize((0.485, 0.456, 0.406),      # normalize image for pre-trained model
                         (0.229, 0.224, 0.225))])

# Build data loader.
data_loader = get_loader(transform=transform_train,
                         mode='train',
                         batch_size=batch_size,
                         vocab_threshold=vocab_threshold,
                         vocab_from_file=vocab_from_file)

# The size of the vocabulary.
vocab_size = len(data_loader.dataset.vocab)

# Initialize the encoder and decoder. 
encoder = EncoderCNN(embed_size)
decoder = DecoderRNN(embed_size, hidden_size, vocab_size)

# Move models to GPU if CUDA is available. 
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
encoder.to(device)
decoder.to(device)

# Define the loss function. 
criterion = nn.CrossEntropyLoss().cuda() if torch.cuda.is_available() else nn.CrossEntropyLoss()

# TODO #3: Specify the learnable parameters of the model.
params = list(decoder.parameters()) + list(encoder.embed.parameters())

# TODO #4: Define the optimizer.
optimizer = torch.optim.Adam(params, lr=0.001)

# Set the total number of training steps per epoch.
total_step = math.ceil(len(data_loader.dataset.caption_lengths) / data_loader.batch_sampler.batch_size)

[nltk_data] Downloading package punkt to /root/nltk_data...
[nltk_data]   Unzipping tokenizers/punkt.zip.
Vocabulary successfully loaded from vocab.pkl file!
loading annotations into memory...
Done (t=1.08s)
creating index...


  0%|          | 744/414113 [00:00<01:57, 3508.23it/s]

index created!
Obtaining caption lengths...


100%|██████████| 414113/414113 [01:35<00:00, 4314.09it/s]
Downloading: "https://download.pytorch.org/models/resnet50-19c8e357.pth" to /root/.torch/models/resnet50-19c8e357.pth
100%|██████████| 102502400/102502400 [00:01<00:00, 91315223.55it/s]
/opt/conda/lib/python3.6/site-packages/torch/nn/modules/rnn.py:38: UserWarning: dropout option adds dropout after all but last recurrent layer, so non-zero dropout expects num_layers greater than 1, but got dropout=0.5 and num_layers=1
  "num_layers={}".format(dropout, num_layers))


<a id='step2'></a>
## Step 2: Train your Model

Once you have executed the code cell in **Step 1**, the training procedure below should run without issue.  

It is completely fine to leave the code cell below as-is without modifications to train your model.  However, if you would like to modify the code used to train the model below, you must ensure that your changes are easily parsed by your reviewer.  In other words, make sure to provide appropriate comments to describe how your code works!  

You may find it useful to load saved weights to resume training.  In that case, note the names of the files containing the encoder and decoder weights that you'd like to load (`encoder_file` and `decoder_file`).  Then you can load the weights by using the lines below:

```python
# Load pre-trained weights before resuming training.
encoder.load_state_dict(torch.load(os.path.join('./models', encoder_file)))
decoder.load_state_dict(torch.load(os.path.join('./models', decoder_file)))
```

While trying out parameters, make sure to take extensive notes and record the settings that you used in your various training runs.  In particular, you don't want to encounter a situation where you've trained a model for several hours but can't remember what settings you used :).

### A Note on Tuning Hyperparameters

To figure out how well your model is doing, you can look at how the training loss and perplexity evolve during training - and for the purposes of this project, you are encouraged to amend the hyperparameters based on this information.  

However, this will not tell you if your model is overfitting to the training data, and, unfortunately, overfitting is a problem that is commonly encountered when training image captioning models.  

For this project, you need not worry about overfitting. **This project does not have strict requirements regarding the performance of your model**, and you just need to demonstrate that your model has learned **_something_** when you generate captions on the test data.  For now, we strongly encourage you to train your model for the suggested 3 epochs without worrying about performance; then, you should immediately transition to the next notebook in the sequence (**3_Inference.ipynb**) to see how your model performs on the test data.  If your model needs to be changed, you can come back to this notebook, amend hyperparameters (if necessary), and re-train the model.

That said, if you would like to go above and beyond in this project, you can read about some approaches to minimizing overfitting in section 4.3.1 of [this paper](http://ieeexplore.ieee.org/stamp/stamp.jsp?arnumber=7505636).  In the next (optional) step of this notebook, we provide some guidance for assessing the performance on the validation dataset.

In [2]:
import torch.utils.data as data
import numpy as np
import os
import requests
import time

# Open the training log file.
f = open(log_file, 'w')
num_epochs = 3             # number of training epochs

old_time = time.time()
response = requests.request("GET", 
                            "http://metadata.google.internal/computeMetadata/v1/instance/attributes/keep_alive_token", 
                            headers={"Metadata-Flavor":"Google"})

for epoch in range(1, num_epochs+1):
    
    for i_step in range(1, total_step+1):
        
        if time.time() - old_time > 60:
            old_time = time.time()
            requests.request("POST", 
                             "https://nebula.udacity.com/api/v1/remote/keep-alive", 
                             headers={'Authorization': "STAR " + response.text})
        
        # Randomly sample a caption length, and sample indices with that length.
        indices = data_loader.dataset.get_train_indices()
        # Create and assign a batch sampler to retrieve a batch with the sampled indices.
        new_sampler = data.sampler.SubsetRandomSampler(indices=indices)
        data_loader.batch_sampler.sampler = new_sampler
        
        # Obtain the batch.
        images, captions = next(iter(data_loader))

        # Move batch of images and captions to GPU if CUDA is available.
        images = images.to(device)
        captions = captions.to(device)
        
        # Zero the gradients.
        decoder.zero_grad()
        encoder.zero_grad()
        
        # Pass the inputs through the CNN-RNN model.
        features = encoder(images)
        outputs = decoder(features, captions)
        
        # Calculate the batch loss.
        loss = criterion(outputs.view(-1, vocab_size), captions.view(-1))
        
        # Backward pass.
        loss.backward()
        
        # Update the parameters in the optimizer.
        optimizer.step()
        
        # Get training statistics.
        stats = 'Epoch [%d/%d], Step [%d/%d], Loss: %.4f, Perplexity: %5.4f' % (epoch, num_epochs, i_step, total_step, loss.item(), np.exp(loss.item()))
        
        # Print training statistics (on same line).
        print('\r' + stats, end="")
        sys.stdout.flush()
        
        # Print training statistics to file.
        f.write(stats + '\n')
        f.flush()
        
        # Print training statistics (on different line).
        if i_step % print_every == 0:
            print('\r' + stats)
            
    # Save the weights.
    if epoch % save_every == 0:
        torch.save(decoder.state_dict(), os.path.join('./models', 'decoder-%d.pkl' % epoch))
        torch.save(encoder.state_dict(), os.path.join('./models', 'encoder-%d.pkl' % epoch))

# Close the training log file.
f.close()


[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [1/25883], Loss: 9.0991, Perplexity: 8947.2290
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [2/25883], Loss: 8.9769, Perplexity: 7917.8299
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [3/25883], Loss: 8.8178, Perplexity: 6753.6520
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [4/25883], Loss: 8.5705, Perplexity: 5273.6624
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [5/25883], Loss: 8.2351, Perplexity: 3771.1133
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [6/25883], Loss: 7.1214, Perplexity: 1238.1335
[model.py] captions_1 torch.Size(

Epoch [1/1], Step [102/25883], Loss: 3.8817, Perplexity: 48.5086
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [103/25883], Loss: 4.1476, Perplexity: 63.2821
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [104/25883], Loss: 4.2417, Perplexity: 69.5257
[model.py] captions_1 torch.Size([16, 19, 256])
[model.py] captions_2 torch.Size([16, 19, 256])
Epoch [1/1], Step [105/25883], Loss: 4.7803, Perplexity: 119.1420
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [106/25883], Loss: 4.1469, Perplexity: 63.2381
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [107/25883], Loss: 3.9719, Perplexity: 53.0858
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [108/25883], Lo

Epoch [1/1], Step [153/25883], Loss: 3.8042, Perplexity: 44.8904
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [154/25883], Loss: 3.9500, Perplexity: 51.9346
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [155/25883], Loss: 4.1036, Perplexity: 60.5583
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [156/25883], Loss: 4.1238, Perplexity: 61.7966
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [157/25883], Loss: 3.6159, Perplexity: 37.1847
[model.py] captions_1 torch.Size([16, 17, 256])
[model.py] captions_2 torch.Size([16, 17, 256])
Epoch [1/1], Step [158/25883], Loss: 4.1807, Perplexity: 65.4130
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [159/25883], Los

Epoch [1/1], Step [204/25883], Loss: 3.4768, Perplexity: 32.3556
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [205/25883], Loss: 3.5259, Perplexity: 33.9853
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [206/25883], Loss: 4.0101, Perplexity: 55.1526
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [207/25883], Loss: 3.8821, Perplexity: 48.5273
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [208/25883], Loss: 3.3384, Perplexity: 28.1751
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [209/25883], Loss: 3.3652, Perplexity: 28.9400
[model.py] captions_1 torch.Size([16, 15, 256])
[model.py] captions_2 torch.Size([16, 15, 256])
Epoch [1/1], Step [210/25883], Los

Epoch [1/1], Step [255/25883], Loss: 3.4327, Perplexity: 30.9606
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [256/25883], Loss: 3.5295, Perplexity: 34.1083
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [257/25883], Loss: 3.3067, Perplexity: 27.2943
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [258/25883], Loss: 3.7372, Perplexity: 41.9805
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [259/25883], Loss: 3.8221, Perplexity: 45.6987
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [260/25883], Loss: 3.2436, Perplexity: 25.6259
[model.py] captions_1 torch.Size([16, 16, 256])
[model.py] captions_2 torch.Size([16, 16, 256])
Epoch [1/1], Step [261/25883], Los

...

Epoch [1/1], Step [25653/25883], Loss: 1.9752, Perplexity: 7.2079
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25654/25883], Loss: 2.0749, Perplexity: 7.9638
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [25655/25883], Loss: 1.7894, Perplexity: 5.9861
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25656/25883], Loss: 1.5530, Perplexity: 4.7256
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25657/25883], Loss: 1.9344, Perplexity: 6.9197
[model.py] captions_1 torch.Size([16, 16, 256])
[model.py] captions_2 torch.Size([16, 16, 256])
Epoch [1/1], Step [25658/25883], Loss: 2.3266, Perplexity: 10.2432
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25659/25

Epoch [1/1], Step [25704/25883], Loss: 2.0268, Perplexity: 7.5897
[model.py] captions_1 torch.Size([16, 9, 256])
[model.py] captions_2 torch.Size([16, 9, 256])
Epoch [1/1], Step [25705/25883], Loss: 2.1372, Perplexity: 8.4759
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25706/25883], Loss: 1.9071, Perplexity: 6.7335
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25707/25883], Loss: 2.3901, Perplexity: 10.9145
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25708/25883], Loss: 1.9949, Perplexity: 7.3517
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25709/25883], Loss: 1.7369, Perplexity: 5.6795
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25710/2588

Epoch [1/1], Step [25755/25883], Loss: 2.0294, Perplexity: 7.6094
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25756/25883], Loss: 1.6345, Perplexity: 5.1267
[model.py] captions_1 torch.Size([16, 16, 256])
[model.py] captions_2 torch.Size([16, 16, 256])
Epoch [1/1], Step [25757/25883], Loss: 2.0293, Perplexity: 7.6088
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25758/25883], Loss: 2.0536, Perplexity: 7.7959
[model.py] captions_1 torch.Size([16, 13, 256])
[model.py] captions_2 torch.Size([16, 13, 256])
Epoch [1/1], Step [25759/25883], Loss: 2.4424, Perplexity: 11.5004
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25760/25883], Loss: 2.1737, Perplexity: 8.7908
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25761/25

Epoch [1/1], Step [25806/25883], Loss: 2.8826, Perplexity: 17.8614
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [25807/25883], Loss: 2.1295, Perplexity: 8.4105
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [25808/25883], Loss: 2.2498, Perplexity: 9.4854
[model.py] captions_1 torch.Size([16, 12, 256])
[model.py] captions_2 torch.Size([16, 12, 256])
Epoch [1/1], Step [25809/25883], Loss: 1.7674, Perplexity: 5.8556
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25810/25883], Loss: 2.2270, Perplexity: 9.2721
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25811/25883], Loss: 1.8176, Perplexity: 6.1568
[model.py] captions_1 torch.Size([16, 15, 256])
[model.py] captions_2 torch.Size([16, 15, 256])
Epoch [1/1], Step [25812/25

Epoch [1/1], Step [25857/25883], Loss: 2.2645, Perplexity: 9.6264
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25858/25883], Loss: 2.0542, Perplexity: 7.8006
[model.py] captions_1 torch.Size([16, 10, 256])
[model.py] captions_2 torch.Size([16, 10, 256])
Epoch [1/1], Step [25859/25883], Loss: 2.0352, Perplexity: 7.6535
[model.py] captions_1 torch.Size([16, 11, 256])
[model.py] captions_2 torch.Size([16, 11, 256])
Epoch [1/1], Step [25860/25883], Loss: 2.0690, Perplexity: 7.9170
[model.py] captions_1 torch.Size([16, 15, 256])
[model.py] captions_2 torch.Size([16, 15, 256])
Epoch [1/1], Step [25861/25883], Loss: 2.1594, Perplexity: 8.6655
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [25862/25883], Loss: 2.3713, Perplexity: 10.7116
[model.py] captions_1 torch.Size([16, 14, 256])
[model.py] captions_2 torch.Size([16, 14, 256])
Epoch [1/1], Step [25863/25

<a id='step3'></a>
## Step 3: (Optional) Validate your Model

To assess potential overfitting, one approach is to assess performance on a validation set.  If you decide to do this **optional** task, you are required to first complete all of the steps in the next notebook in the sequence (**3_Inference.ipynb**); as part of that notebook, you will write and test code (specifically, the `sample` method in the `DecoderRNN` class) that uses your RNN decoder to generate captions.  That code will prove incredibly useful here. 

If you decide to validate your model, please do not edit the data loader in **data_loader.py**.  Instead, create a new file named **data_loader_val.py** containing the code for obtaining the data loader for the validation data.  You can access:
- the validation images at filepath `'/opt/cocoapi/images/train2014/'`, and
- the validation image caption annotation file at filepath `'/opt/cocoapi/annotations/captions_val2014.json'`.

The suggested approach to validating your model involves creating a json file such as [this one](https://github.com/cocodataset/cocoapi/blob/master/results/captions_val2014_fakecap_results.json) containing your model's predicted captions for the validation images.  Then, you can write your own script or use one that you [find online](https://github.com/tylin/coco-caption) to calculate the BLEU score of your model.  You can read more about the BLEU score, along with other evaluation metrics (such as TEOR and Cider) in section 4.1 of [this paper](https://arxiv.org/pdf/1411.4555.pdf).  For more information about how to use the annotation file, check out the [website](http://cocodataset.org/#download) for the COCO dataset.

In [1]:
# (Optional) TODO: Validate your model.

**note:** I did not do step 3